## Imports

In [1]:
import googlemaps
import pandas as pd
import numpy as np
import re
import os
import geopandas as gpd
import folium

## Links

Miami-Dade data download: https://gis-mdc.opendata.arcgis.com/datasets/MDC::property-boundary-view/about
DOR Use code descriptions: https://gis-mdc.opendata.arcgis.com/datasets/MDC::dor-code/explore

Palm Beach data download: https://opendata2-pbcgov.opendata.arcgis.com/datasets/PBCGOV::property-information-table/explore

Broward Property Appraiser "Contact Us" page: https://bcpa.net/phone.asp

## Data read-in

In [24]:
MiamiDade = gpd.read_file('Property_Boundary_View.geojson')
PalmBeach = pd.read_csv('Property_Information_Table.csv',dtype='str')

## Data Check

In [25]:
MD_agri = MiamiDade[MiamiDade['DOR_DESC'].str.contains('AGRI',na=False)]

In [26]:
PB_agri = PalmBeach[PalmBeach['PROPERTY_USE'].str.contains('AGRI',na=False)]

## Make Map

In [28]:
MD_agri['COLOR'] = 'blue'
PB_agri['COLOR'] = 'orange'

/Users/afarence/opt/anaconda3/lib/python3.9/site-packages/geopandas/geodataframe.py:1472: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
/var/folders/rq/0_j_rksd7psgdycg9c1qwf6m0000gp/T/ipykernel_66819/4005685728.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  PB_agri['COLOR'] = 'orange'


In [29]:
def popup_html_MD(row):
    address = row['TRUE_SITE_ADDR']
    folio = row['FOLIO']
    
    html = '''<!DOCTYPE html>
    <html>
    <strong>Address: </strong>{}'''.format(address) + '''<br>
    <strong>Folio: </strong>{}'''.format(folio) + '''<br>
    </html>
    '''
    return html

def popup_html_PB(row):
    address = row['SITE_ADDR_STR']
    folio = row['PARCEL_NUMBER']
    
    html = '''<!DOCTYPE html>
    <html>
    <strong>Address: </strong>{}'''.format(address) + '''<br>
    <strong>Folio: </strong>{}'''.format(folio) + '''<br>
    </html>
    '''
    return html

## Geocode

In [7]:
# %store -r google_maps_API_Key
# gmaps_key = googlemaps.Client(key=google_maps_API_Key)

In [8]:
# PB_agri['full_address'] = PB_agri['SITE_ADDR_STR'] + ' Palm Beach County, FL'

In [9]:
# def geocode(add):
#     g = gmaps_key.geocode(add)
#     lat = g[0]["geometry"]["location"]["lat"]
#     lng = g[0]["geometry"]["location"]["lng"]
#     return (lat, lng)

# PB_agri['geocoded'] = PB_agri['full_address'].apply(geocode)

In [30]:
# MD_agri[['X_COORD','Y_COORD']] = MD_agri[['X_COORD','Y_COORD']].astype(float)
# MD_agri['X_COORD'] = MD_agri['X_COORD'] * -1

In [31]:
MD_agri[['X_COORD','Y_COORD']]

X_COORD   Y_COORD
14453   922105.9  534685.7
30293   922991.6  546593.2
30944   923041.7  546818.5
62433   904755.7  505310.9
87146   897698.5  500965.2
...          ...       ...
528614  883589.0  463612.8
538171  909929.4  585401.0
538173  909921.1  585568.4
572489  880358.1  458923.7
572496  879496.4  460502.3

[3023 rows x 2 columns]

In [40]:
### Create map container ###
m = folium.Map(location=[MD_agri.centroid.y.mean(), MD_agri.centroid.x.mean()], zoom_start=10)

title_html = '''
              <h3 align="center" style="font-size:16px"><b>{}</b></h3>
             '''.format(f'South Florida Agricultural Properties')

# Add the GeoJSON layer to the map
folium.GeoJson(MD_agri.to_json(),
               name='geojson',
               popup=folium.features.GeoJsonPopup(fields=['TRUE_SITE_ADDR', 'FOLIO'])
              ).add_to(m)

m.get_root().html.add_child(folium.Element(title_html))
            
# Display map
m

/var/folders/rq/0_j_rksd7psgdycg9c1qwf6m0000gp/T/ipykernel_66819/2573231373.py:2: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  m = folium.Map(location=[MD_agri.centroid.y.mean(), MD_agri.centroid.x.mean()], zoom_start=10)
/var/folders/rq/0_j_rksd7psgdycg9c1qwf6m0000gp/T/ipykernel_66819/2573231373.py:2: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  m = folium.Map(location=[MD_agri.centroid.y.mean(), MD_agri.centroid.x.mean()], zoom_start=10)
